In [2]:
import os
import pandas as pd
import numpy as np
import sklearn

from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.model_selection import train_test_split

import nltk
# nltk.download('stopwords')
# nltk.download('wordnet')
# nltk.download('punkt')
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from nltk.stem import PorterStemmer
from nltk.stem import WordNetLemmatizer
import string
from wordcloud import WordCloud, STOPWORDS

# import plotly.express as px
import matplotlib.pyplot as plt

from sklearn.naive_bayes import BernoulliNB


import numpy as np
import pandas as pd
# BeautifulSoup is used to remove html tags from the text
from bs4 import BeautifulSoup 
import re # For regular expressions

# Packages for data 
import pandas as pd
import numpy as np
import pickle
from collections import Counter

# Packages for machine learning modelling
from sklearn.decomposition import TruncatedSVD
from sklearn.model_selection import train_test_split
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
from sklearn.naive_bayes import BernoulliNB
from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import AdaBoostClassifier

from sklearn.metrics import classification_report,confusion_matrix, ConfusionMatrixDisplay, accuracy_score
# precision_score, recall_score, f1_score

from sklearn.pipeline import Pipeline
from sklearn.pipeline import FeatureUnion

# Packages for sentiment analysis
from textblob import TextBlob

# Packages for visualisation 
import matplotlib.pyplot as plt

# Packages for MLP
import nltk

import gensim
from gensim.models import word2vec
import gensim.downloader as api

In [3]:
# Load data

train_data = pd.read_csv("../Data/train_data.csv")
val_data = pd.read_csv("../Data/validation_data.csv")
test_data = pd.read_csv("../Data/test_data.csv")

X_train_text = train_data["text_preprocessed"].values
y_train = train_data["class_label"].values

X_val_text = val_data["text_preprocessed"].values
y_val = val_data["class_label"].values

X_test_text = test_data["text_preprocessed"].values
y_test = test_data["class_label"].values

In [4]:
# Create list of lists of Unigrams based on training corpus
lst_corpus = []
for string in X_train_text:
    lst_words = string.split()
    lst_grams = [" ".join(lst_words[i:i+1]) 
                for i in range(0, len(lst_words), 1)]
    lst_corpus.append(lst_grams)

In [5]:
# Find mean length
num_articles = len(lst_corpus)
total_len = 0
for article in lst_corpus:
    total_len += len(article)

print('mean length =', total_len/num_articles)

mean length = 311.68333333333334


In [5]:
# Creating the model and setting values for the various parameters
corpus = lst_corpus # Must be a list of lists of tokens
num_features = 300  # Word vector dimensionality, i.e. target size of word vectors
min_word_count = 10 # Minimum word count
num_workers = 4     # Number of parallel threads
context = 311        # Context window size, possible to use mean length of text in corpus
downsampling = 1e-3 # (0.001) Downsample setting for frequent words
skipgram = 1 # Use skipgram = 1

# Initializing the train model
model = word2vec.Word2Vec(
    sentences = corpus,
    workers=num_workers,
    size=num_features,
    min_count=min_word_count,
    window=context,
    sample=downsampling,
    sg=skipgram
)

# To make the model memory efficient
model.init_sims(replace=True)

# Saving the model for later use. Can be loaded using Word2Vec.load()
model_name = "300features_10minwords_311context_skip"
model.save(model_name)
print("model saved")


TypeError: __init__() got an unexpected keyword argument 'size'

# Load Model

In [6]:
# Load pre-trained Word2Vec model.
# model = gensim.models.Word2Vec.load('300features_40minwords_10context')
# model = gensim.models.Word2Vec.load('300features_10minwords_311context')
model = gensim.models.Word2Vec.load('Pretrained_Word2Vec/300features_10minwords_311context_skip')

In [7]:
# gensim 3.x
# words = list(model.wv.vocab) 
# print('length of vocab:', len(words))

words = len(model.wv)
print('length of vocab:', words)

length of vocab: 29926


In [8]:
# Example of similar words
w1="trump"
model.wv.most_similar(positive=w1)

[('donald', 0.9013703465461731),
 ('republican', 0.7219638824462891),
 ('presid', 0.7009391188621521),
 ('presidenti', 0.6926494836807251),
 ('campaign', 0.6864993572235107),
 ('support', 0.6612122058868408),
 ('candid', 0.6407409310340881),
 ('nomine', 0.601711630821228),
 ('democrat', 0.5973963737487793),
 ('obama', 0.5808975696563721)]

In [8]:
# # Create word_vec dictionary, gensim 3.x
# word_vec = dict({})
# for idx, key, in enumerate(model.wv.vocab):
#     word_vec[key] = model.wv[key]
# # print("input word vectors:")
# # print(word_vec)

# Create word_vec dictionary, gensim 4
word_vec = dict({})
for word, idx in model.wv.key_to_index.items():
    word_vec[word] = model.wv[idx]
# print("input word vectors:")
# # print(word_vec)

In [13]:
# model.wv.key_to_index

In [14]:
word_vec
# model.wv.get_vecattr("rock", "count")
# model.wv['rock']

{'german': array([ 9.73564088e-02,  4.91774343e-02, -6.82038367e-02,  2.48755310e-02,
         2.43646409e-02,  5.71707264e-02,  1.44551307e-01,  1.85174439e-02,
         1.11793824e-01,  9.64799523e-02, -2.78815348e-02,  5.34992851e-02,
        -4.44417028e-03, -7.47384550e-03, -7.95844644e-02,  1.14562690e-01,
        -2.80500650e-02,  1.46677613e-03,  1.02522522e-02, -5.85265793e-02,
         9.61758792e-02,  1.57645103e-02, -1.10270739e-01, -4.23760228e-02,
         4.47286852e-03, -1.01905512e-02,  7.22354874e-02,  6.76257117e-03,
        -1.31515130e-01, -8.31619203e-02,  4.83022369e-02, -3.34844552e-02,
        -1.02918735e-02, -1.00978063e-02, -1.67669542e-02,  1.84999984e-02,
         2.83427862e-03, -5.44000007e-02, -6.39815331e-02, -6.90949336e-02,
         1.35710491e-02,  7.85451010e-02,  6.98015094e-03, -4.72444519e-02,
        -5.75662851e-02, -7.21621513e-02, -3.72998342e-02,  1.26143709e-01,
        -1.05215525e-02, -8.03866312e-02, -9.29665926e-04,  3.77071882e-03,
  

In [15]:
len(word_vec)

29926

### Generate document vectors

In [9]:
# Train
X_train = []
text = X_train_text
for i in range(len(text)):
    doc_vec_for_each_sent = np.array(300)
    for j in range(len(text[i])):
        word = text[i][j]
        if word in word_vec.keys():
            doc_vec_for_each_sent = np.add(doc_vec_for_each_sent,
                                            word_vec[word])
    doc_vec_for_each_sent = np.divide(doc_vec_for_each_sent, len(text[i]))
    X_train.append(doc_vec_for_each_sent)
# print('Generated Document Vectors:')
# print(X_train)
print(len(X_train))
print(len(text))

39060
39060


In [10]:
# Val
X_val = []
text = X_val_text
for i in range(len(text)):
    doc_vec_for_each_sent = np.array(300)
    for j in range(len(text[i])):
        word = text[i][j]
        if word in word_vec.keys():
            doc_vec_for_each_sent = np.add(doc_vec_for_each_sent,
                                            word_vec[word])
    doc_vec_for_each_sent = np.divide(doc_vec_for_each_sent, len(text[i]))
    X_val.append(doc_vec_for_each_sent)
# print('Generated Document Vectors:')
# print(X_val)
print(len(X_val))
print(len(text))

13020
13020


In [11]:
# Test
X_test = []
text = X_test_text
for i in range(len(text)):
    doc_vec_for_each_sent = np.array(300)
    for j in range(len(text[i])):
        word = text[i][j]
        if word in word_vec.keys():
            doc_vec_for_each_sent = np.add(doc_vec_for_each_sent,
                                            word_vec[word])
    doc_vec_for_each_sent = np.divide(doc_vec_for_each_sent, len(text[i]))
    X_test.append(doc_vec_for_each_sent)
# print('Generated Document Vectors:')
# print(X_test)
print(len(X_test))
print(len(text))

13021
13021


### Modelling

In [12]:
# Logreg
log_reg_clf = LogisticRegression()
log_reg_clf.fit(X_train, y_train)

y_val_pred = log_reg_clf.predict(X_val)
print(classification_report(y_val, y_val_pred))

              precision    recall  f1-score   support

           0       0.66      0.67      0.66      6361
           1       0.68      0.68      0.68      6659

    accuracy                           0.67     13020
   macro avg       0.67      0.67      0.67     13020
weighted avg       0.67      0.67      0.67     13020



In [16]:
# NB
naive_bayes_clf = BernoulliNB()
naive_bayes_clf.fit(X_train, y_train)

y_test_pred = naive_bayes_clf.predict(X_test)
print(classification_report(y_test, y_test_pred))

              precision    recall  f1-score   support

           0       0.49      0.97      0.65      6361
           1       0.57      0.04      0.08      6660

    accuracy                           0.49     13021
   macro avg       0.53      0.50      0.37     13021
weighted avg       0.53      0.49      0.36     13021



In [15]:
adaboost_clf = AdaBoostClassifier(random_state = 1) # n_estimators
adaboost_clf.fit(X_train, y_train)

y_val_pred = adaboost_clf.predict(X_val)
print(classification_report(y_val, y_val_pred))

KeyboardInterrupt: 

### Using pretrained Word2Vec

In [20]:
X_train_text[0]

'german wage talk includ new focu reduc work hour frankfurtberlin reuter trade union powerhous won 35hour work week german two decad ago mobil new campaign reduc work hour annual wage negoti kick nationwid ig metal germani s biggest union 23 million worker mainli car manufactur industri say shorter hour will help shift worker need care children elderli rel wide implic german societi evolv 21st centuri union s gambit success economist count strong wage rise will watch see deflationari effect domest consumpt overtak export driver euro zone s biggest economi union begin intern discuss local level thursday campaign germani s parliamentari elect enter final phase issu work famili high agenda time made order wage round issu will great support societi ig metal presid joerg hofmann told union confer late june launch initi valu time valu money will carri equal weight hofmann told journalist last week ig metal will releas nation list demand end octob negoti employ begin novemb buoy record employ

In [21]:
# Train
docs_vectors = pd.DataFrame() # creating empty final dataframe
stopwords = nltk.corpus.stopwords.words('english') # removing stop words
for doc in X_train_text: # looping through each document
    temp = pd.DataFrame()  # creating a temporary dataframe(store value for 1st doc & for 2nd doc remove the details of 1st & proceed through 2nd and so on..)
    for word in doc.split(' '): # looping through each word of a single document and spliting through space
        if word not in stopwords: # if word is not present in stopwords then (try)
            try:
                word_vector = model[word] # if word is present in embeddings(google provides weights associate with words(300)) then proceed
                temp = temp.append(pd.Series(word_vector), ignore_index = True) # if word is present then append it to temporary dataframe
            except:
                pass
    doc_vector = temp.mean() # take the average of each column(w0, w1, w2,........w300)
    docs_vectors = docs_vectors.append(doc_vector, ignore_index = True) # append each document value to the final dataframe
docs_vectors.shape

<ipython-input-21-76b174c02074>:8: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  word_vector = model[word] # if word is present in embeddings(google provides weights associate with words(300)) then proceed


In [ ]:
# Val
X_val2 = pd.DataFrame() # creating empty final dataframe

for doc in X_val_text: # looping through each document
    temp = pd.DataFrame()  # creating a temporary dataframe(store value for 1st doc & for 2nd doc remove the details of 1st & proceed through 2nd and so on..)
    for word in doc.split(' '): # looping through each word of a single document and spliting through space
        try:
            word_vector = model[word] # if word is present in embeddings(google provides weights associate with words(300)) then proceed
            temp = temp.append(pd.Series(word_vector), ignore_index = True) # if word is present then append it to temporary dataframe
        except:
            pass
    doc_vector = temp.mean() # take the average of each column(w0, w1, w2,........w300)
    X_val2 = X_val2.append(doc_vector, ignore_index = True) # append each document value to the final dataframe
X_val2.shape

In [ ]:
pd.isnull(docs_vectors).sum().sum()

In [ ]:
# Logreg
log_reg_clf = LogisticRegression()
log_reg_clf.fit(docs_vectors, y_train)

y_val_pred = log_reg_clf.predict(X_val2)
print(classification_report(y_val, y_val_pred))